
# 1/ Deploying our first AI Agent (RAG) application with Mosaic AI Agent Framework & Agent Evaluation

<img src="https://github.com/prasadkona/databricks_demos/blob/main/images/llm-rag-full-unstructuredio.png?raw=true" style="width: 800px; margin-left: 10px">

<br/>

## From data to chatbot in 10 minutes

Rag applications are decoupled in 2 main parts:
- The knowledge database used to add additional context and improve the bot answer
- The actual chatbot application and its review / feedback mechanism

## 1.1/ Data preparation for RAG: building and indexing our knowledge base into Databricks Vector Search

Let's start by prepraing our knowledge database. In this simple first demo, we will use UnstructuredIO to extract files from one of the 20+ sources supported. UnstructuredIO supports 70+file types. Unstructured IO extracts files from the sources, extracts text, transforms, enriches it with embeddings and delivers the consumption ready data to the Databricks as a table. 

They can automatically sync new files that get created on the supported sources and update the Databricks tavles accordingly.


In [0]:
%pip install -U --quiet databricks-sdk==0.49.0 "databricks-langchain>=0.4.0" databricks-agents mlflow[databricks] databricks-vectorsearch==0.55 langchain==0.3.19 langchain_core==0.3.37 bs4==0.0.2 markdownify==0.14.1 pydantic==2.10.1
%pip install openai

dbutils.library.restartPython()

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
%run ../_resources/00-init $reset_all_data=false

Following are set in config file used by the 00-init. Update thse parameters to reflect your environment.

* catalog = "prasad_kona_isv"
* dbName = db = "demo"
* VECTOR_SEARCH_ENDPOINT_NAME="one-env-shared-endpoint-6"
* vs_index_name ="prasad_unstructuredio_demo_index"


Create table statement for UnstructuredIO (for reference)


% sql 
-- Create table statement for data ingested by UnstructuredIO
CREATE TABLE if not exists prasad_kona_isv.demo.unstructuredio_demo_table (
  id STRING NOT NULL,
  record_id STRING NOT NULL,
  element_id STRING NOT NULL,
  text STRING,
  embeddings ARRAY<FLOAT>,
  type STRING,
  metadata VARIANT,
  text_as_html STRING GENERATED ALWAYS AS (COALESCE(get_json_object(CAST(metadata AS STRING), '$.text_as_html'), '')),
  filename   STRING GENERATED ALWAYS AS (COALESCE(get_json_object(CAST(metadata AS STRING), '$.filename'), '')), 
  CONSTRAINT `unstructuredio_demo_table_pk` PRIMARY KEY (`id`))
USING delta
TBLPROPERTIES (
  'delta.checkpoint.writeStatsAsJson' = 'false',
  'delta.checkpoint.writeStatsAsStruct' = 'true',
  'delta.enableDeletionVectors' = 'true',
  'delta.feature.appendOnly' = 'supported',
  'delta.feature.deletionVectors' = 'supported',
  'delta.feature.invariants' = 'supported',
  'delta.feature.variantType-preview' = 'supported',
  'delta.minReaderVersion' = '3',
  'delta.minWriterVersion' = '7');

-- Enable change data feed. This is required for vector search
ALTER TABLE `prasad_kona_isv`.`demo`.`unstructuredio_demo_table_v2` SET TBLPROPERTIES (delta.enableChangeDataFeed = true);



In [0]:
%sql 
-- The dataset for your knowledge base has been loaded for you by UnstructuredIO.

SELECT * FROM prasad_kona_isv.demo.unstructuredio_demo_table

id record_id element_id text embeddings type metadata text_as_html filename 34d32059-0c0e-54a4-8f71-3148fb028d2c fe56aacb-07ee-52c5-b813-d842602a2c70 8930a57f597a605be16ce97bc10d0121 Table of Contents

UNITED STATES SECURITIES AND EXCHANGE COMMISSION

Washington, D.C. 20549

FORM 10-K

ANNUAL REPORT PURSUANT TO SECTION 13 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934 For the fiscal year ended August 28, 2022 or TRANSITION REPORT PURSUANT TO SECTION 13 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934 Commission file number 0-20355

Costco Wholesale Corporation

(Exact name of registrant as specified in its charter) List(-0.0075606247, -0.0101201795, -0.0016540808, 0.018028704, -0.0033236928, -0.05362639, -0.011232219, 0.03600771, -0.010058054, 0.06833761, 0.004066088, -0.020787058, -0.0055943653, -0.06769151, -0.040406168, 0.022563837, -0.051936585, -0.017332904, 0.02465124, 0.014686374, 0.009144815, 0.03546101, 0.022911737, 0.05491859, 0.040058266, -5.032133E-4, 0.002921433, 0.02497429, 0.031286202, 0.026962293, 0.04801028, 0.0051967646, -0.017531704, 0.0032988428, 0.019979432, 0.024899742, 0.0033516493, 0.027036844, 0.0042151883, 0.0041592754, -0.0132326465, 0.0014956618, -0.027757496, 0.078426726, -0.010343829, -0.014077548, 0.021271635, -0.02193016, -0.016773777, -0.011033418, 0.012195158, -0.03526221, -0.0020268315, 0.019296056, -3.3974665E-4, 0.0030379174, 0.053278487, 0.04669323, -0.004308376, 0.013133246, 0.010548842, -0.02148286, 0.018028704, 0.002325032, 0.006833761, 0.017755354, -0.03826906, -7.090027E-4, 0.016637102, -0.020563409, -0.009548628, -0.025371892, 0.007920951, 0.0015065337, 0.05571379, -0.032727502, 0.0042058695, -0.004382926, 0.040754065, 0.0022566942, 0.006796486, 0.013456297, 0.034889456, 0.024763066, -0.022973863, -0.020998284, -0.03071465, -0.09214395, -0.025160667, 0.028304197, 0.039586116, -0.016301626, -0.0102754915, 0.0069580115, 0.03081405, 0.04286632, -0.045326475, 0.015568551, 0.006585261, -0.0014032507, 0.017519278, 0.013158097, -0.0052775275, 0.018115679, -0.007163024, 0.033100255, 0.012685946, 0.0044264137, -0.0091013275, 0.028155096, 0.03533676, 0.028403597, -0.011120393, 0.011288131, -0.009076477, -0.020203084, 0.0053365463, 0.04279177, 0.008070051, 0.0073369746, 0.0074363747, -0.039909165, 0.024589116, -0.029298197, 0.019171806, 0.018575406, 0.0058366535, -0.007989288, -0.016289202, 0.0036746997, -0.053129386, 0.023346614, -0.04408397, -0.00925664, -0.02120951, -0.022476861, 0.011095543, -0.014276348, 0.011368894, 0.0046531702, -0.00777185, -0.015494, 0.041226216, 0.011797557, -0.033796057, -0.011182519, -0.011816194, -0.0075482, 0.0066535985, -0.008896315, 0.033671804, -0.002545576, 0.0022240786, -0.014375748, 0.009088903, -0.0029556018, 0.03150985, 0.010753855, -0.008188088, 0.0011656223, -6.2008615E-4, 0.03633076, -0.025719792, -0.032578405, 0.0308886, -0.0036125747, 0.07057411, 0.0042058695, 0.016724078, 0.009964867, 0.008424164, -0.009387103, -0.025844043, -0.044531275, 0.006815124, 0.0028701797, 0.028627247, 0.0155934, 0.008598114, 0.016612252, 0.020290058, 0.025943443, 0.034814905, -0.014512423, -0.03106255, -0.033994857, 0.0014335368, 0.0048892456, 0.012039845, 0.0062839543, 0.002373179, 0.039710365, 0.046568975, -0.009014352, -0.020998284, -0.010033204, 0.017034702, 0.01596615, -0.011629819, -1.1781928E-5, 0.026365893, 0.010548842, 0.04167352, 0.009511353, 0.020066408, 8.542201E-4, 0.005727934, 0.0033112678, -0.004681126, 0.013779348, -0.019979432, -0.013170522, 0.035162807, 0.023843614, 0.011679519, 0.01819023, -0.009113752, -0.021097684, -0.0025719793, -0.0015663292, 0.016661953, -0.028751496, 0.016363751, 0.0061317477, 0.0015554572, -0.026042843, 0.0087969145, 0.009492716, -0.0061348537, 0.04838303, 5.036016E-4, -0.0605347, -0.07847643, 0.0030876175, -0.008169451, -0.010101542, -0.0031714865, -0.014736074, -0.027335044, -0.011809981, 0.012772921, 0.0045227073, 8.92563E-5, 0.00925664, 0.016873177, -0.007933375, 0.0151958, 0.06803941, 0.04286632, 0.02445244, 0.008778277, 0.025


## 1.2/ Vector search Endpoints

Vector search endpoints are entities where your indexes will live. Think about them as entry point to handle your search request. 

Let's start by creating our first Vector Search endpoint. Once created, you can view it in the [Vector Search Endpoints UI](#/setting/clusters/vector-search). Click on the endpoint name to see all indexes that are served by the endpoint.

Reference code to creating "Vector Search endpoint"

`
from databricks.vector_search.client import VectorSearchClient
vsc = VectorSearchClient(disable_notice=True)

if not endpoint_exists(vsc, VECTOR_SEARCH_ENDPOINT_NAME):
    vsc.create_endpoint(name=VECTOR_SEARCH_ENDPOINT_NAME, endpoint_type="STANDARD")

wait_for_vs_endpoint_to_be_ready(vsc, VECTOR_SEARCH_ENDPOINT_NAME)
print(f"Endpoint named {VECTOR_SEARCH_ENDPOINT_NAME} is ready.")
`


<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/rag-basic-prep-3.png?raw=true" style="float: right; margin-left: 10px" width="400px">


## 1.3/ Creating the Vector Search Index

Once the endpoint is created, all we now have to do is to as Databricks to create the index on top of the existing table. 

You just need to specify the text column and our embedding foundation model.  Databricks will build and synchronize the index automatically for us.

This can be done using the API, or in a few clicks within the Unity Catalog Explorer menu:

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/index_creation.gif?raw=true" width="600px">


Reference code to creating "Vector Search index"


from databricks.sdk import WorkspaceClient
import databricks.sdk.service.catalog as c

`#`The table we'd like to index
source_table_fullname = f"{catalog}.{db}.databricks_documentation"
`#`Where we want to store our index
vs_index_fullname = f"{catalog}.{db}.databricks_documentation_vs_index"

if not index_exists(vsc, VECTOR_SEARCH_ENDPOINT_NAME, vs_index_fullname):
  print(f"Creating index {vs_index_fullname} on endpoint {VECTOR_SEARCH_ENDPOINT_NAME}...")
  vsc.create_delta_sync_index(
    endpoint_name=VECTOR_SEARCH_ENDPOINT_NAME,
    index_name=vs_index_fullname,
    source_table_name=source_table_fullname,
    pipeline_type="TRIGGERED",
    primary_key="id",
    embedding_source_column='content', #The column containing our text
    embedding_model_endpoint_name='databricks-gte-large-en' #The embedding endpoint used to create the embeddings
  )
  `#`Let's wait for the index to be ready and all our embeddings to be created and indexed
  wait_for_index_to_be_ready(vsc, VECTOR_SEARCH_ENDPOINT_NAME, vs_index_fullname)
else:
  `#`Trigger a sync to update our vs content with the new data saved in the table
  wait_for_index_to_be_ready(vsc, VECTOR_SEARCH_ENDPOINT_NAME, vs_index_fullname)
  vsc.get_index(VECTOR_SEARCH_ENDPOINT_NAME, vs_index_fullname).sync()

print(f"index {vs_index_fullname} on table {source_table_fullname} is ready")
`

## 1.4/ Searching for relevant content

That's all we have to do. Databricks can automatically capture and synchronize new entries in your table with the index. You can also trig the sync's as needed.

Note that depending on your dataset size and model size, index creation can take a few seconds to start and index your embeddings.

Let's give it a try and search for similar content.

*Note: `similarity_search` also support a filters parameter. This is useful to add a security layer to your RAG system: you can filter out some sensitive content based on who is doing the call (for example filter on a specific department based on the user preference).*

In [0]:
from databricks.vector_search.client import VectorSearchClient
vsc = VectorSearchClient(disable_notice=True)

vs_index_fullname = f"{catalog}.{db}.{vs_index_name}"

DEBUG_FLAG=False

In [0]:
from mlflow.deployments import get_deploy_client

# Embedding models like bge-large-en Foundation models are available using the /serving-endpoints/databricks-bge-large-en/invocations api. 
deploy_client = get_deploy_client("databricks")
embeddings = deploy_client.predict(endpoint="databricks-bge-large-en", inputs={"input": ["What is Apache Spark?"]})

#print(embeddings)

In [0]:
# UDF for embedding
from pyspark.sql.types import *
def get_embedding_for_string(text):
    response = deploy_client.predict(endpoint="agents-demo-embeddings-large", inputs={"input": text})
    e = response.data
    return e[0]['embedding']

get_embedding_for_string_udf = udf(get_embedding_for_string, ArrayType(FloatType()))
#print(get_embedding_for_string("What is a lakehouse ?"))

INFO:py4j.clientserver:Received command c on object id p0


In [0]:
# Using langchain DatabricksEmbeddings
from databricks_langchain import DatabricksEmbeddings

embed = DatabricksEmbeddings(
    endpoint="agents-demo-embeddings-large",
)

#print(embeddings)


In [0]:
# Get vector search index details via api
if(DEBUG_FLAG)
  x =vsc.get_index(VECTOR_SEARCH_ENDPOINT_NAME, vs_index_fullname)
  print(x.describe())

INFO:py4j.clientserver:Received command c on object id p0


{'name': 'prasad_kona_isv.demo.prasad_unstructuredio_demo_index', 'endpoint_name': 'one-env-shared-endpoint-6', 'primary_key': 'id', 'index_type': 'DELTA_SYNC', 'delta_sync_index_spec': {'source_table': 'prasad_kona_isv.demo.unstructuredio_demo_table', 'embedding_vector_columns': [{'name': 'embeddings', 'embedding_dimension': 3072}], 'pipeline_type': 'TRIGGERED', 'pipeline_id': 'c1659de6-1252-435a-b4e7-381c927634be'}, 'status': {'detailed_state': 'ONLINE_NO_PENDING_UPDATE', 'message': 'Index creation succeeded. Check latest status: https://e2-demo-field-eng.cloud.databricks.com/explore/data/prasad_kona_isv/demo/prasad_unstructuredio_demo_index', 'indexed_row_count': 1581, 'triggered_update_status': {'last_processed_commit_version': 11, 'last_processed_commit_timestamp': '2025-04-28T19:09:34Z'}, 'ready': True, 'index_url': 'e2-demo-field-eng.cloud.databricks.com/api/2.0/vector-search/indexes/prasad_kona_isv.demo.prasad_unstructuredio_demo_index'}, 'creator': 'prasad.kona@databricks.com'

In [0]:
question = "what is walmarts revenue in 2022?"

# Assuming you have a function to convert the question to a query vector
#query_vector = get_embedding_for_string(question)
query_vector = embed.embed_query(question)

results = vsc.get_index(VECTOR_SEARCH_ENDPOINT_NAME, vs_index_fullname).similarity_search(
  query_vector=query_vector,
  columns=[ "id","text","filename","type","text_as_html"],
  num_results=3)
docs = results.get('result', {}).get('data_array', [])
docs

INFO:py4j.clientserver:Received command c on object id p0


[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.


[['8b704986-f77b-5c69-9947-5a651b386ef6',
  'y 31, 2020 ("fiscal 2020"). During fiscal 2022, we generated total revenues of $572.8 billion, which was comprised primarily of net sales of $567.8 billion. We maintain our principal offices in Bentonville, Arkansas. Our common stock trades on the New York Stock Exchange under the symbol "WMT."',
  'WALMART_2022_10K.pdf',
  'CompositeElement',
  '<p class="NarrativeText" id="ca70934faeb540dd884b61b1c3b91576">Walmart Inc. ("Walmart," the "Company" or "we") helps people around the world save money and live better – anytime and anywhere – by providing the opportunity to shop in both retail stores and through eCommerce, and to access our other service offerings. Through innovation, we strive to continuously improve a customer-centric experience that seamlessly integrates our eCommerce and retail stores in an omni-channel offering that saves time for our customers. Each week, we serve approximately 230 million customers who visit more than 10,500

# 2/ Deploy our chatbot model with RAG using Llama

<img src="https://github.com/prasadkona/databricks_demos/blob/main/images/llm-rag-full-unstructuredio-2.png?raw=true" style="float: right" width="500px">

We've seen how UnstructuredIO and Databricks makes it easy to ingest, prepare your documents, and deploy a Vector Search index on top of it.

Now that our Vector Search index is ready, let's deploy a langchain application.

## 2.1/ Configuring our Chain parameters

As any appliaction, a RAG chain needs some configuration for each environement (ex: different catalog for test/prod environement). 

Databricks makes this easy with Chain Configurations. You can use this object to configure any value within your app, including the different system prompts and make it easy to test and deploy newer version with better prompt.

In [0]:
# For this first basic demo, we'll keep the configuration as a minimum. In real app, you can make all your RAG as a param (such as your prompt template to easily test different prompts!)
chain_config = {
    "llm_model_serving_endpoint_name": "databricks-llama-4-maverick",  # the foundation model we want to use
    "embedding_model":"agents-demo-embeddings-large",
    "vector_search_endpoint_name": VECTOR_SEARCH_ENDPOINT_NAME,  # the endoint we want to use for vector search
    "vector_search_index": f"{catalog}.{db}.{vs_index_name}",
    "llm_prompt_template": """You are an assistant that answers questions. Use the following pieces of retrieved context to answer the question. Some pieces of context may be irrelevant, in which case you should not use them to form the answer.\n\nContext: {context}""",
}

### 2.2 Building our Langchain retriever

<img src="https://github.com/prasadkona/databricks_demos/blob/main/images/llm-rag-full-unstructuredio-2.png?raw=true" style="float: right" width="500px">

Let's start by building our Langchain retriever. 

It will be in charge of:

* Creating the input question (compute the embeddings using MosaicAI foundational models)
* Calling the vector search index to find similar documents to augment the prompt with 

Databricks Langchain wrapper makes it easy to do in one step, handling all the underlying logic and API call for you.

In [0]:
from databricks.vector_search.client import VectorSearchClient
from databricks_langchain.vectorstores import DatabricksVectorSearch
from langchain.schema.runnable import RunnableLambda
from langchain_core.output_parsers import StrOutputParser

## Enable MLflow Tracing
mlflow.langchain.autolog()

## Load the chain's configuration
model_config = mlflow.models.ModelConfig(development_config=chain_config)

## Turn the Vector Search index into a LangChain retriever
vector_search_as_retriever = DatabricksVectorSearch(
    endpoint=model_config.get("vector_search_endpoint_name"),
    index_name=model_config.get("vector_search_index"),
    columns=["id","text","filename","type","text_as_html"],
    text_column="text",
    embedding = DatabricksEmbeddings(
                    endpoint=model_config.get("embedding_model"),
                )
).as_retriever(search_kwargs={"k": 3})

# Method to format the docs returned by the retriever into the prompt (keep only the text from chunks)
def format_context(docs):
    chunk_contents = [f"Passage: {d.page_content}\n" for d in docs]
    return "".join(chunk_contents)

#Let's try our retriever chain:
relevant_docs = (vector_search_as_retriever | RunnableLambda(format_context)| StrOutputParser()).invoke('What was costco revenue in 2022?')

display_txt_as_html(relevant_docs)

INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0


[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.


Passage: Item 1—Business Costco Wholesale Corporation and its subsidiaries (Costco or the Company) began operations in 1983, in Seattle, Washington. We are principally engaged in the operation of membership warehouses in the United States (U.S.) and Puerto Rico, Canada, Mexico, Japan, United Kingdom (U.K.), Korea, Taiwan, Australia, Spain, France, China, and Iceland. Costco operated 838, 815, and 795 warehouses worldwide at August 28, 2022, August 29, 2021, and August 30, 2020, respectively. The Company operates e-commerce websites in the U.S., Canada, Mexico, U.K., Korea, Taiwan, Japan, and Australia. Our common stock trades on the NASDAQ Global Select Market, under the symbol “COST.” We report on a 52/53-week fiscal year, consisting of thirteen four-week periods and ending on the Sunday nearest the end of August. The first three quarters consist of three periods each, and the fourth quarter consists of four periods (five weeks in the thirteenth period in a 53-week year). The material seasonal impact in our operations is increased net sales and earnings during the winter holiday season. References to 2022, 2021, and 2020 relate to the 52-week fiscal years ended August 28, 2022, August 29, 2021, and August 30, 2020, respectively. Passage: Net Sales 2022 2021 2020 Net Sales $ 222,730 $ 192,052 $ 163,220 Increases in net sales: U.S. 17 % 16 % 9 % Canada 16 % 22 % 5 % Other International 10 % 23 % 13 % Total Company 16 % 18 % 9 % Increases in comparable sales: U.S. 16 % 15 % 8 % Canada 15 % 20 % 5 % Other International 7 % 19 % 9 % Total Company 14 % 16 % 8 % Increases in comparable sales excluding the impact of changes in foreign currency and gasoline prices: U.S. 10 % 14 % 9 % Canada 12 % 12 % 7 % Other International 10 % 13 % 11 % Total Company 11 % 13 % 9 % Net Sales Net sales increased $30,678 or 16% during 2022. The improvement was attributable to an increase in comparable sales of 14%, and sales at new warehouses opened in 2021 and 2022. Sales increased $15,830 in core merchandise categories and $14,848 in warehouse ancillary and other businesses. The rate of increase was strongest in our gasoline, business centers, and travel businesses. Sales continued to be impacted by inflation, higher than what we experienced in previous fiscal years. During 2022, higher gasoline prices positively impacted net sales by $9,230, 481 basis points, compared to 2021, with a 42% increase in the average price per gallon. The volume of gasoline sold increased approximately 22%, positively impacting net sales by $3,847, 200 basis points. Changes in foreign currencies relative to the U.S. dollar negatively impacted net sales by approximately $1,762, 92 basis points, compared to 2021, attributable primarily to our Other International operations. Comparable Sales Comparable sales increased 14% during 2022 and were positively impacted by increases in shopping frequency and average ticket, which includes the effects of inflation and changes in foreign currency. E-commerce comparable sales increased 10% during 2022, including inflation. 25 Table of Contents Passage: Highlights for 2022 versus 2021 include: We opened 26 new warehouses, including 3 relocations: 14 net new in the U.S., 2 net new in our Canadian segment, and 7 new in our Other International segment, compared to 22 new warehouses, including 2 relocations in 2021; Net sales increased 16% to $222,730 driven by a 14% increase in comparable sales and sales at new warehouses opened in 2021 and 2022; Membership fee revenue increased 9% to $4,224, driven by new member sign-ups, upgrades to Executive membership, and an increase in our renewal rate; Gross margin percentage decreased 65 basis points, driven primarily by our core merchandise categories and a LIFO charge for higher merchandise costs; SG&A expenses as a percentage of net sales decreased 77 basis points, primarily due to leveraging increased sales and ceasing of incremental wages related to COVID-19, despite additional wage and benefi

Trace(request_id=tr-19d94399949f4c43bda5b56d03525c3d)

You can see in the results that Databricks automatically trace your chain details and you can debug each steps and review the documents retrieved.

## 2.3/ Building Databricks Chat Model to query our demo's Foundational LLM

<img src="https://github.com/prasadkona/databricks_demos/blob/main/images/llm-rag-full-unstructuredio-2.png?raw=true" style="float: right" width="500px">

Our chatbot will be using Meta's Llama open source model. However, it could be utilized with any other LLMs supported on Databricks.  

Other types of models that could be utilized include:

- Databricks Foundation models (_what we will use by default in this demo_)
- Your organization's custom, fine-tuned model
- An external model provider (_such as Azure OpenAI_)


In [0]:
from langchain_core.prompts import ChatPromptTemplate
from databricks_langchain.chat_models import ChatDatabricks
from operator import itemgetter

prompt = ChatPromptTemplate.from_messages(
    [  
        ("system", model_config.get("llm_prompt_template")), # Contains the instructions from the configuration
        ("user", "{question}") #user's questions
    ]
)

# Our foundation model answering the final prompt
model = ChatDatabricks(
    endpoint=model_config.get("llm_model_serving_endpoint_name"),
    extra_params={"temperature": 0.01, "max_tokens": 500}
)

#Let's try our prompt:
answer = (prompt | model | StrOutputParser()).invoke({'question':'What was revenue in 2022 for pepsi?', 'context': ''})
display_txt_as_html(answer)

INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clie

For the fiscal year 2022, PepsiCo reported revenues of $86.4 billion.

Trace(request_id=tr-6acc0bcaa1544885ab677ca712013786)


## 2.4/ Putting it together in a final chain, supporting the standard Chat Completion format

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/rag-basic-chain-4.png?raw=true" style="float: right" width="500px">


Let's now merge the retriever and the model in a single Langchain chain.

We will use a custom langchain template for our assistant to give proper answer.

We will make sure our chain support the standard Chat Completion API input schema : `{"messages": [{"role": "user", "content": "What is Retrieval-augmented Generation?"}]}`

Make sure you take some time to try different templates and adjust your assistant tone and personality for your requirement.

*Note that we won't support history in this first version, and will only take the last message as the question. See the advanced demo for a more complete example.*

In [0]:
# Return the string contents of the most recent messages: [{...}] from the user to be used as input question
def extract_user_query_string(chat_messages_array):
    return chat_messages_array[-1]["content"]

# RAG Chain
chain = (
    {
        "question": itemgetter("messages") | RunnableLambda(extract_user_query_string),
        "context": itemgetter("messages")
        | RunnableLambda(extract_user_query_string)
        | vector_search_as_retriever
        | RunnableLambda(format_context),
    }
    | prompt
    | model
    | StrOutputParser()
)


#### Databricks will track all the chain for you

<img src="https://ai-cookbook.io/_images/mlflow_trace2.gif" width="600px" style="float: right; margin-left: 10px">

As you can see in the cell result below, Databricks automatically trace the chain call. 

This makes it super easy to debug and improve your chain!

In [0]:
# Let's give it a try:
input_example = {"messages": [ {"role": "user", "content": "What was revenue in 2022 for pepsi?"}]}
answer = chain.invoke(input_example)
print(answer)

INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Closing down clientserver connection
INFO:py4j.clientserver:Closing down clientserver connection


[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.


INFO:py4j.clientserver:Received command c on object id p0


According to the Consolidated Statement of Income, the Net Revenue for PepsiCo, Inc. and Subsidiaries in 2022 was $86,392 million.


Trace(request_id=tr-0a25e498e84c4b11af10235d1d27a133)

## 2.5/ Deploy a RAG Chain to a web-based UI for stakeholder feedback

Our chain is now ready! 

Let's first register the Rag Chain model to MLFlow and Unity Catalog, and then use Agent Framework to deploy to the Agent Evaluation stakeholder review application which is backed by a scalable, production-ready Model Serving endpoint.

In [0]:
from mlflow.models.resources import DatabricksVectorSearchIndex, DatabricksServingEndpoint
# Log the model to MLflow
with mlflow.start_run(run_name="pkona_rag_bot"):
  logged_chain_info = mlflow.langchain.log_model(
          #Note: In classical ML, MLflow works by serializing the model object.  In generative AI, chains often include Python packages that do not serialize.  Here, we use MLflow's new code-based logging, where we saved our chain under the chain notebook and will use this code instead of trying to serialize the object.
          lc_model=os.path.join(os.getcwd(), 'chain'),  # Chain code file e.g., /path/to/the/chain.py 
          model_config=chain_config, # Chain configuration 
          artifact_path="chain", # Required by MLflow, the chain's code/config are saved in this directory
          input_example=input_example,
          example_no_conversion=True,  # Required by MLflow to use the input_example as the chain's schema,
          # Specify resources for automatic authentication passthrough
          resources=[
            DatabricksVectorSearchIndex(index_name=model_config.get("vector_search_index")),
            DatabricksServingEndpoint(endpoint_name=model_config.get("embedding_model")),
            DatabricksServingEndpoint(endpoint_name=model_config.get("llm_model_serving_endpoint_name"))
          ]
      )

MODEL_NAME = "pkona_rag_demo"
MODEL_NAME_FQN = f"{catalog}.{db}.{MODEL_NAME}"
# Register to UC
uc_registered_model_info = mlflow.register_model(model_uri=logged_chain_info.model_uri, name=MODEL_NAME_FQN)

INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0


[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.


INFO:py4j.clientserver:Closing down clientserver connection
INFO:py4j.clientserver:Closing down clientserver connection
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Closing down clientserver connection
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Closing down clientserver connection
INFO:p

[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.


INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clie

...

INFO:py4j.clientserver:Received command c on object id p0


Registered model 'prasad_kona_isv.demo.pkona_rag_demo' already exists. Creating a new version of this model...
INFO:py4j.clientserver:Received command c on object id p0


INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Closing down clientserver connection
INFO:py4j.clientserver:Closing down clientserver connection
INFO:py4j.clientserver:Closing down clientserver connection
INFO:py4j.clientserver:Closing down clientserver connection
INFO:py4j.clientserver:Closing down clientserver connection
INFO:py4j.clientserver:Closing down clientserver connection
INFO:py4j.clientserver:Closing down clientserver connection
INFO:py4j.clientserver:Closing down clientserver connection


Uploading artifacts:   0%|          | 0/12 [00:00<?, ?it/s]

Created version '3' of model 'prasad_kona_isv.demo.pkona_rag_demo'.
INFO:py4j.clientserver:Received command c on object id p0


Let's now deploy the Mosaic AI **Agent Evaluation review application** using the model we just created!

In [0]:
from databricks import agents
# Deploy to enable the Review APP and create an API endpoint
# Note: scaling down to zero will provide unexpected behavior for the chat app. Set it to false for a prod-ready application.
deployment_info = agents.deploy(MODEL_NAME_FQN, model_version=uc_registered_model_info.version, scale_to_zero=True)

instructions_to_reviewer = f"""## Instructions for Testing the AI chatbot

Your inputs are invaluable for the development team. By providing detailed feedback and corrections, you help us fix issues and improve the overall quality of the application. We rely on your expertise to identify any gaps or areas needing enhancement."""

# Add the user-facing instructions to the Review App
agents.set_review_instructions(MODEL_NAME_FQN, instructions_to_reviewer)

wait_for_model_serving_endpoint_to_be_ready(deployment_info.endpoint_name)

INFO:py4j.clientserver:Received command c on object id p0


INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0



    Deployment of prasad_kona_isv.demo.pkona_rag_demo version 3 initiated.  This can take up to 15 minutes and the Review App & Query Endpoint will not work until this deployment finishes.

    View status: https://e2-demo-field-eng.cloud.databricks.com/ml/endpoints/agents_prasad_kona_isv-demo-pkona_rag_demo
    Review App: https://e2-demo-field-eng.cloud.databricks.com/ml/review-v2/308f204122a04044a9fe43c8c97b1bac/chat
Waiting for endpoint to deploy agents_prasad_kona_isv-demo-pkona_rag_demo. Current state: EndpointState(config_update=<EndpointStateConfigUpdate.IN_PROGRESS: 'IN_PROGRESS'>, ready=<EndpointStateReady.NOT_READY: 'NOT_READY'>)


INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clie

Waiting for endpoint to deploy agents_prasad_kona_isv-demo-pkona_rag_demo. Current state: EndpointState(config_update=<EndpointStateConfigUpdate.IN_PROGRESS: 'IN_PROGRESS'>, ready=<EndpointStateReady.NOT_READY: 'NOT_READY'>)


INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clientserver:Received command c on object id p0
INFO:py4j.clie

endpoint ready.


INFO:py4j.clientserver:Received command c on object id p0


# 3/ Use the Mosaic AI Agent Evaluation to evaluate your RAG applications

## 3.1/ Chat with your bot and build your validation dataset!

Our Chat Bot is now live. Databricks provides a built-in chatbot application that you can use to test the chatbot and give feedbacks on its answer.

You can easily give access to external domain experts and have them test and review the bot.  **Your domain experts do NOT need to have Databricks Workspace access** - you can assign permissions to any user in your SSO if you have enabled [SCIM](https://docs.databricks.com/en/admin/users-groups/scim/index.html)

This is a critical step to build or improve your evaluation dataset: have users ask questions to your bot, and provide the bot with output answer when they don't answer properly.

Your Chatbot is automatically capturing all stakeholder questions and bot responses, including an MLflow trace for each, into Delta Tables in your Lakehouse. On top of that, Databricks makes it easy to track feedback from your end user: if the chatbot doesn't give a good answer and the user gives a thumbdown, their feedback is included in the Delta Tables.

Once your eval dataset is ready, you'll then be able to leverage it for offline evaluation to measure your new chatbot performance, and also potentially to Fine Tune your model.
<br/>

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/chatbot-rag/eval-framework.gif?raw=true" width="1000px">


In [0]:
print(f"\n\nReview App URL to share with your stakeholders: {deployment_info.review_app_url}")



Review App URL to share with your stakeholders: https://e2-demo-field-eng.cloud.databricks.com/ml/review-v2/308f204122a04044a9fe43c8c97b1bac/chat



## 3.2/ Evaluate your bot's quality with Mosaic AI Agent Evaluation specialized LLM judge models

Our bot is now Live. 

Evaluation is a key part of deploying a RAG application. Databricks simplify this tasks with specialized LLM models tuned to evaluate your bot's quality/cost/latency, even if ground truth is not available.

Mosaic AI Agent Evaluation evaluates:
1. Answer correctness - requires ground truth
2. Hallucination / groundness - no ground truth required
3. Answer relevance - no ground truth required
4. Retrieval precision - no ground truth required
5. (Lack of) Toxicity - no ground truth required

In this example, we'll use an evaluation set that we curated based on our internal experts using the Mosaic AI Agent Evaluation review app interface.  This proper Eval Dataset is saved as a Delta Table.

To see how to collect the dataset from the Eval App, see the [https://notebooks.databricks.com/demos/llm-rag-chatbot/index.html] => 03-advanced-app/03-Offline-Evaluation notebook.

Reference code for eval

eval_dataset = spark.table("eval_set_databricks_documentation").limit(10).toPandas()
display(eval_dataset)

## 3.1/ Run Evaluation of your Chain

Let's leverage the Mosaic AI Agent Evaluation specialized LLM to evaluate our model performance (make sure you use `databricks-rag`):

Reference code to run eval on your chain

with mlflow.start_run(run_id=logged_chain_info.run_id):
    # Evaluate the logged model
    eval_results = mlflow.evaluate(
        data=eval_dataset,
        model=logged_chain_info.model_uri,
        model_type="databricks-agent",
    )


You can open your MLFlow Experiment to review the different evaluation, and compare multiple model response to see how different prompts answer: 

<img src="https://github.com/prasadkona/databricks_demos/blob/main/images/rag-mlflow-eval.png?raw=true" width="1200px">

## Next: 

This is the end of this simple demo. 
